In [1]:
# Dependencies
import requests
import json
import pandas as pd

In [2]:
#check url response
apikey ="f98921da60b71947056633acb25f5147"
search_url = f"https://developers.zomato.com/api/v2.1/search?entity_id=259&entity_type=city"
print(requests.get(search_url, headers={"user-key" : apikey}))



<Response [200]>


In [3]:
#check data structure
# Retrieving data and converting it into JSON
data = requests.get(search_url, headers={"user-key" : apikey}).json()
#display data structure
data


{'results_found': 17504,
 'results_start': 0,
 'results_shown': 20,
 'restaurants': [{'restaurant': {'R': {'has_menu_status': {'delivery': -1,
      'takeaway': -1},
     'res_id': 16577492,
     'is_grocery_store': False},
    'apikey': 'f98921da60b71947056633acb25f5147',
    'id': '16577492',
    'name': 'Chin Chin',
    'url': 'https://www.zomato.com/melbourne/chin-chin-3-cbd?utm_source=api_basic_user&utm_medium=api&utm_campaign=v2.1',
    'location': {'address': '125 Flinders Lane, CBD, Melbourne',
     'locality': 'CBD',
     'city': 'Melbourne',
     'city_id': 259,
     'latitude': '-37.8155645773',
     'longitude': '144.9703757465',
     'zipcode': '3000',
     'country_id': 14,
     'locality_verbose': 'CBD, Melbourne'},
    'switch_to_order_menu': 0,
    'cuisines': 'Thai, Asian Fusion',
    'timings': '11 AM to 11 PM (Mon-Thu, Sun), 11 AM to 11:30 PM (Fri-Sat)',
    'average_cost_for_two': 135,
    'price_range': 4,
    'currency': '$',
    'highlights': ['Dinner',
     'Cr

In [4]:
resto_num = data["results_found"]
print(f"Number of Rest: {resto_num}")

Number of Rest: 17502


In [5]:
#single city 
#print(json.dumps(data, indent=4, sort_keys=True))

rest_id_list = []
rest_name_list =[]
rest_cuis_list = []
rest_local_list = []
rest_city_list = []
rest_rate_list = []
rest_delivery_list = []
rest_ratenum_list = []

resto_num = 20
show_page = 0

citynum =259

search_url = f"https://developers.zomato.com/api/v2.1/search?entity_id={citynum}&entity_type=city&start={show_page}"
data = requests.get(search_url, headers={"user-key" : apikey}).json()
for page in range(5):
    for count in range(resto_num):
        try: 
            rest_id = data["restaurants"][count]["restaurant"]["id"]
            rest_name = data["restaurants"][count]["restaurant"]["name"]
            rest_cuis = data["restaurants"][count]["restaurant"]["cuisines"]
            rest_local = data["restaurants"][count]["restaurant"]["location"]["locality"]
            rest_city = data["restaurants"][count]["restaurant"]["location"]["city"]
            rest_rate_num = data["restaurants"][count]["restaurant"]["all_reviews_count"]
            rest_rate = data["restaurants"][count]["restaurant"]["user_rating"]["aggregate_rating"]
            rest_delivery = data["restaurants"][count]["restaurant"]["highlights"]
            
            #check if current restaurant does delivery 
            theydelivery = False
            for doesdelivery in rest_delivery:
                if doesdelivery == 'Delivery':
                    theydelivery = True
            
            if theydelivery == True:
                rest_delivery = "Yes"
            else:
                rest_delivery = "No"
            
            #append to list
            rest_id_list.append(rest_id)
            rest_name_list.append(rest_name)
            rest_cuis_list.append(rest_cuis)
            rest_local_list.append(rest_local)
            rest_city_list.append(rest_city)
            rest_rate_list.append(rest_rate)
            rest_ratenum_list.append(rest_rate_num)
            rest_delivery_list.append(rest_delivery)
            
            #go to next page
            if count == 19:
                show_page = show_page + 20
                search_url = f"https://developers.zomato.com/api/v2.1/search?entity_id={citynum}&entity_type=city&start={show_page}"
                data = requests.get(search_url, headers={"user-key" : apikey}).json()
                count = 0
        except:
            print("error")
#check errors when making dataframe
try:            
    restaurants_df = pd.DataFrame({
        "Restaurant ID":rest_id_list,
        "Name":rest_name_list,
        "Cuisine":rest_cuis_list,
        "Locality":rest_local_list,
        "City":rest_city_list,
        "Rating":rest_rate_list,
        "Total Number Ratings": rest_ratenum_list,
        "Delivery":rest_delivery_list
    })
except:
    print(len(rest_id_list))
    print(len(rest_name_list))
    print(len(rest_cuis_list))
    print(len(rest_local_list))
    print(len(rest_city_list))
    print(len(rest_rate_list))
    print(len(rest_review_list))
    print(len(rest_delivery_list))
    

restaurants_df

Restaurant ID                            Name  \
0       16577492                       Chin Chin   
1       16585905                         Tipo 00   
2       16577212                         Beatrix   
3       16583098              Lune Croissanterie   
4       16573665            The Hardware Societe   
..           ...                             ...   
95      16574121                         Don Don   
96      16582908               Mugen Ramen & Bar   
97      16586156  The Grand Trailer Park Taverna   
98      16579874             Two Birds One Stone   
99      16573068             HuTong Dumpling Bar   

                                         Cuisine         Locality       City  \
0                             Thai, Asian Fusion              CBD  Melbourne   
1                                        Italian              CBD  Melbourne   
2                         Coffee and Tea, Bakery  North Melbourne  Melbourne   
3                                 Bakery, French          Fitzroy  Melbourne   
4              French, Cafe Food, Coffee and Tea              CBD  Melbourne   
..                                           ...              ...        ...   
95                               Japanese, Asian              CBD  Melbourne   
96                               Japanese, Ramen              CBD  Melbourne   
97                              Burger, American              CBD  Melbourne   
98  Coffee and Tea, Modern Australian, Cafe Food      South Yarra  Melbourne   
99                                       Chinese              CBD  Melbourne   

   Rating  Total Number Ratings Delivery  
0     4.6                  3206       No  
1     4.9                   721       No  
2     4.9                   384       No  
3     4.9                   753       No  
4     4.6                  2103       No  
..    ...                   ...      ...  
95    4.6                   692      Yes  
96    4.4                   349       No  
97    4.4                   668      Yes  
98    4.4                   684       No  
99    4.3                  1167       No  

[100 rows x 8 columns]

In [6]:
#save dataframe single city to csv
restaurants_df = restaurants_df.drop_duplicates()
restaurants_df.to_csv("single_restaurant_data.csv", encoding="utf-8", index=False)

In [21]:
#multiple cities
#Perth,Melbourne,Sydney,Brisbane,Adelaide,Gold Coast,Canberra(ACT),Newcastle,Wollongong,Logan City(Village),Geelong
#print(json.dumps(data, indent=4, sort_keys=True))
cityid = [296,259,260,298,297,2555,313,2246,2171,2493,1701]

rest_id_list = []
rest_name_list =[]
rest_cuis_list = []
rest_local_list = []
rest_city_list = []
rest_rate_list = []
rest_delivery_list = []
rest_ratenum_list = []
rest_lat_list = []
rest_long_list = []

resto_num = 20
loop_num = 0
show_page = 0

for citynum in cityid:
    search_url = f"https://developers.zomato.com/api/v2.1/search?entity_id={citynum}&entity_type=city&start={show_page}"
    data = requests.get(search_url, headers={"user-key" : apikey}).json()
    for page in range(5):
        for count in range(resto_num):
            try: 
                rest_id = data["restaurants"][count]["restaurant"]["id"]
                rest_name = data["restaurants"][count]["restaurant"]["name"]
                rest_cuis = data["restaurants"][count]["restaurant"]["cuisines"]
                rest_local = data["restaurants"][count]["restaurant"]["location"]["locality"]
                rest_city = data["restaurants"][count]["restaurant"]["location"]["city"]
                rest_lat = data["restaurants"][count]["restaurant"]["location"]["latitude"]
                rest_long = data["restaurants"][count]["restaurant"]["location"]["longitude"]
                rest_rate_num = data["restaurants"][count]["restaurant"]["all_reviews_count"]
                rest_rate = data["restaurants"][count]["restaurant"]["user_rating"]["aggregate_rating"]
                rest_delivery = data["restaurants"][count]["restaurant"]["highlights"]
                
                #check if current restaurant does delivery 
                theydelivery = False
                for doesdelivery in rest_delivery:
                    if doesdelivery == 'Delivery':
                        theydelivery = True

                if theydelivery == True:
                    rest_delivery = "Yes"
                else:
                    rest_delivery = "No"

                #append to list
                rest_id_list.append(rest_id)
                rest_name_list.append(rest_name)
                rest_cuis_list.append(rest_cuis)
                rest_local_list.append(rest_local)
                rest_city_list.append(rest_city)
                rest_rate_list.append(rest_rate)
                rest_ratenum_list.append(rest_rate_num)
                rest_delivery_list.append(rest_delivery)
                rest_lat_list.append(rest_lat)
                rest_long_list.append(rest_long)
                #go to next page
                if count == 19:
                    show_page = show_page + 20
                    search_url = f"https://developers.zomato.com/api/v2.1/search?entity_id={citynum}&entity_type=city&start={show_page}"
                    data = requests.get(search_url, headers={"user-key" : apikey}).json()
                    count = 0
            except:
                print("error")
    count = 0
    page = 0
    show_page = 0


#check errors when making dataframe
try:            
    restaurants_df = pd.DataFrame({
        "Restaurant ID":rest_id_list,
        "Name":rest_name_list,
        "Cuisine":rest_cuis_list,
        "Locality":rest_local_list,
        "City":rest_city_list,
        "Rating":rest_rate_list,
        "Total Number Ratings": rest_ratenum_list,
        "Delivery":rest_delivery_list,
        "Latitude":rest_lat_list,
        "Longitude":rest_long_list
    })
except:
    print(len(rest_id_list))
    print(len(rest_name_list))
    print(len(rest_cuis_list))
    print(len(rest_local_list))
    print(len(rest_city_list))
    print(len(rest_rate_list))
    print(len(rest_review_list))
    print(len(rest_delivery_list))
restaurants_df = restaurants_df.drop_duplicates()
restaurants_df

Restaurant ID                        Name  \
0         16600038                Bib & Tucker   
1         16597645                      Mrs. S   
2         18196379                       tbsp.   
3         16598431              Tuck Shop Cafe   
4         16599082               Sayers Sister   
...            ...                         ...   
1095      16604478  Kohinoor Indian Restaurant   
1096      16606497      The Geelong Boat House   
1097      16607360                Feed My Mojo   
1098      18397507    Rook : Sri Lankan Fusion   
1099      16605366                     Sushi 8   

                                   Cuisine         Locality     City Rating  \
0             Modern Australian, Cafe Food  North Fremantle    Perth    4.1   
1                    Patisserie, Cafe Food         Maylands    Perth    4.5   
2      Sandwich, Coffee and Tea, Cafe Food        Bayswater    Perth    4.7   
3             Modern Australian, Cafe Food      Northbridge    Perth    4.8   
4        Modern Australian, Coffee and Tea        Perth CBD    Perth    4.6   
...                                    ...              ...      ...    ...   
1095                                Indian      Geelong CBD  Geelong    3.8   
1096                               Seafood      Geelong CBD  Geelong    3.2   
1097  Coffee and Tea, Fast Food, Cafe Food          Belmont  Geelong    3.9   
1098                 Sri Lankan, Cafe Food      Geelong CBD  Geelong    3.8   
1099                       Japanese, Sushi      Geelong CBD  Geelong    3.9   

      Total Number Ratings Delivery        Latitude       Longitude  
0                      692       No  -32.0284215000  115.7498293000  
1                      643       No  -31.9286800875  115.8919624239  
2                      335       No  -31.9194560000  115.9096643000  
3                      799       No  -31.9467356499  115.8621080965  
4                      496       No  -31.9404785312  115.8615736663  
...                    ...      ...             ...             ...  
1095                    29       No  -38.1479230000  144.3637390000  
1096                    18       No  -38.1428964000  144.3605468000  
1097                    26       No  -38.1703540000  144.3485380000  
1098                    19      Yes  -38.1479093911  144.3625134230  
1099                    15       No  -38.1491644374  144.3595361710  

[1040 rows x 10 columns]

In [22]:
restaurants_df["City"].value_counts()

Brisbane              101
Perth                 100
Sydney                100
Adelaide              100
Gold Coast            100
Newcastle             100
Wollongong            100
ACT                   100
Melbourne             100
Geelong               100
Eagle Heights           5
Ormeau                  4
Canungra                3
North Tamborine         3
Beaudesert              3
Logan Village           3
Stapylton               3
Advancetown             2
Tamborine               2
Tamborine Mountain      2
Willow Vale             1
Mount Nathan            1
Jimboomba               1
Mount Tamborine         1
Wongawallan             1
Mt Tamborine            1
Springbrook             1
Alberton                1
Beechmont               1
Name: City, dtype: int64

In [23]:
#save dataframe multi city to csv 
restaurants_df = restaurants_df.drop_duplicates()
restaurants_df.to_csv("multi_restaurant_data.csv", encoding="utf-8", index=False)

In [11]:
#check deliveries
restaurants_df["Delivery"].value_counts()

No     273
Yes     27
Name: Delivery, dtype: int64

In [12]:
restaurants_df = restaurants_df.sort_values(by=["Rating"],ascending=False)
restaurants_df

Restaurant ID                              Name  \
138      17881527                            Dexter   
263      15545439               Manpuku - Chatswood   
139      16582574            Hinoki Japanese Pantry   
229      16559171                         Tetsuya's   
232      16558798                              Quay   
..            ...                               ...   
38       16600326                Mary Street Bakery   
78       16601688                           Tropico   
58       16599918                   Jamie's Italian   
89       16598361                 The Wild Fig Cafe   
88       16601603  Lucky Chan's Laundry + Noodlebar   

                             Cuisine       Locality       City Rating  \
138                    American, BBQ        Preston  Melbourne    4.9   
263                  Japanese, Ramen      Chatswood     Sydney    4.9   
139                  Japanese, Sushi        Fitzroy  Melbourne    4.9   
229                         Japanese            CBD     Sydney    4.9   
232                Modern Australian  Circular Quay     Sydney    4.9   
..                               ...            ...        ...    ...   
38                            Bakery       Highgate      Perth    4.0   
78   Tapas, Modern Australian, Pizza    North Beach      Perth    4.0   
58                           Italian      Perth CBD      Perth    3.8   
89      Modern Australian, Cafe Food    Scarborough      Perth    3.3   
88                   Asian, Bar Food    Northbridge      Perth    2.9   

     Total Number Ratings Delivery  
138                   684       No  
263                   196       No  
139                   271       No  
229                   330       No  
232                   451       No  
..                    ...      ...  
38                    518       No  
78                    302       No  
58                   1473       No  
89                    709       No  
88                    388       No  

[300 rows x 8 columns]

In [13]:
#get top restaurant per city
perth_top = restaurants_df.loc[restaurants_df["City"]=="Perth"]
perth_top = perth_top.head()
perth_top

Restaurant ID                   Name                               Cuisine  \
71      16598976                 Marumo  Japanese, Seafood, Modern Australian   
41      16598837               Run Amuk                             Fast Food   
8       16597513  Pacific Rim Mix Plate                    Hawaiian, Japanese   
60      16596002   Galileo Buona Cucina                               Italian   
23      16598168             Nobu Perth                       Japanese, Sushi   

                          Locality   City Rating  Total Number Ratings  \
71                        Nedlands  Perth    4.9                   141   
41  Orient Street, South Fremantle  Perth    4.9                   341   
8                       Applecross  Perth    4.9                   213   
60                    Shenton Park  Perth    4.8                   207   
23                        Burswood  Perth    4.8                   663   

   Delivery  
71       No  
41       No  
8        No  
60       No  
23       No

In [4]:
#get csv files
#study data files
multi_city = "multi_restaurant_data.csv"

#set data to data frame
multi_df = pd.read_csv(multi_city)
multi_id = multi_df["Restaurant ID"].tolist()
multi_id

[16600038,
 16597645,
 18196379,
 16598431,
 16599082,
 16595894,
 16596036,
 16599032,
 16600553,
 16596238,
 16597513,
 16596903,
 16600511,
 16599893,
 18016553,
 16600889,
 16599949,
 16596362,
 16597137,
 16598699,
 16599765,
 16596244,
 16601597,
 16598168,
 16596306,
 16596815,
 16597030,
 16600113,
 16595944,
 16600681,
 16595766,
 16600128,
 16599597,
 16599574,
 16596860,
 16598588,
 16600792,
 16599599,
 16598048,
 16601401,
 16598837,
 16600326,
 16598045,
 16597765,
 16596635,
 16597791,
 16600310,
 16596818,
 16596980,
 16595831,
 16596581,
 16599234,
 16596548,
 16597128,
 16596534,
 16596768,
 16596072,
 16597087,
 16599918,
 16596002,
 16596945,
 16596567,
 16599146,
 16596448,
 16596981,
 16596326,
 16598876,
 16598952,
 16597131,
 16596479,
 16598976,
 16598601,
 16596234,
 16602022,
 16599605,
 18156128,
 16597743,
 16601688,
 16596049,
 16599238,
 16597986,
 16598970,
 16597786,
 16598736,
 16597253,
 16597153,
 16598361,
 17841646,
 16598265,
 16601603,
 16596615,

In [5]:
#multiple cities
#Perth,Melbourne,Sydney,Brisbane,Adelaide,Gold Coast,Canberra(ACT),Newcastle,Wollongong,Logan City(Village),Geelong
#print(json.dumps(data, indent=4, sort_keys=True))
resto_id = multi_id

rest_id_list = []
rev_rate_list =[]
rev_time_list = []

resto_num = 20
loop_num = 0
show_page = 0
counter = 0
for resnum in resto_id:
    counter = counter + 1
    search_url = f"https://developers.zomato.com/api/v2.1/reviews?res_id={resnum}&start={show_page}"
    data = requests.get(search_url, headers={"user-key" : apikey}).json()
    for page in range(5):
        try:
            for count in range(resto_num):
                try: 
                    rev_rating = data["user_reviews"][count]["review"]["rating"]
                    rev_times = data["user_reviews"][count]["review"]["timestamp"]
                    rest_id = resnum

                    #append to list
                    rest_id_list.append(rest_id)
                    rev_rate_list.append(rev_rating)
                    rev_time_list.append(rev_times)

                    #go to next page
                    if count == 5:
                        show_page = count + 5
                        search_url = f"https://developers.zomato.com/api/v2.1/reviews?res_id={resnum}&start={show_page}"
                        data = requests.get(search_url, headers={"user-key" : apikey}).json()
                        count = 0
                except Exception as e: 
                    print(f"Error Count:{counter} Resto_ID:{resnum}")
                    print(f"Error: {e}")
        except:
            print("Index Error")
    count = 0
    page = 0
    show_page = 0


#check errors when making dataframe 
try:            
    restaurants_df = pd.DataFrame({
        "Restaurant ID":rest_id_list,
        "Rating":rev_rate_list,
        "TimeStamp":rev_time_list,
    })
except:
    print(len(rest_id_list))
    print(len(rest_name_list))
    print(len(rest_cuis_list))

restaurants_df = restaurants_df.drop_duplicates()
restaurants_df

Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out of range
Error Count:1 Resto_ID:16600038
Error: list index out o

Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out of range
Error Count:3 Resto_ID:18196379
Error: list index out o

Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out of range
Error Count:5 Resto_ID:16599082
Error: list index out o

Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out of range
Error Count:7 Resto_ID:16596036
Error: list index out o

Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out of range
Error Count:9 Resto_ID:16600553
Error: list index out o

...

Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606552
Error: 'user_reviews'
Error Count:1033 Resto_ID:16606

Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661318
Error: 'user_reviews'
Error Count:1035 Resto_ID:18661

Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606497
Error: 'user_reviews'
Error Count:1037 Resto_ID:16606

Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397507
Error: 'user_reviews'
Error Count:1039 Resto_ID:18397

Restaurant ID  Rating   TimeStamp
0          16600038     4.5  1600924854
1          16600038     4.0  1594512772
2          16600038     4.0  1582484130
3          16600038     4.0  1578563989
4          16600038     5.0  1576830546
...             ...     ...         ...
8800       16593278     3.0  1598836934
8801       16593278     5.0  1596487540
8802       16593278     4.0  1584554500
8803       16593278     4.0  1584355245
8804       16593278     5.0  1579651748

[1765 rows x 3 columns]

In [6]:
restaurants_df.to_csv("Restaurant_ratingstimestamp_data.csv", encoding="utf-8", index=False)